# 🖥️ W08 Lecture Demo - First practice with database and SQL

**DS105A W08 Lecture – Data for Data Science (Autumn Term 2025/2026)**

<div style="font-family: system-ui; padding: 20px 30px 20px 20px; background-color: #FFFFFF; color: #212121; border-left: 8px solid #2D6C87; border-radius: 8px; box-shadow: 0 4px 12px rgba(0, 0, 0, 0.1);max-width:600px;">

**Lecture Demonstration Notebook**

- 📅 Date: 20 November 2025  
- 👤 Instructor: Dr Jon Cardoso-Silva  
- 💽 Dataset: `imdb_2025.db` (curated subset with `endYear = 2025`)

<span style="display:block;line-height:1.15em;color:#666666;font-size:0.9em;">

🥅 **Learning Goals**

 i) Connect to a SQLite database with `sqlite3`,  
 ii) Run `SELECT`, `WHERE`, and `ORDER BY` queries via `pd.read_sql()`,  
 iii) Retrieve the top 10 titles from `title_rankings` (setup for Friday’s lab synthesis).

</span>

</div>

## What you'll do today

- Open the exact database explored in the slides (`imdb_2025.db`)
- List tables, write a few `SELECT … WHERE …` queries
- Finish with a ranked list using the `title_rankings` table (foreshadows COUNT/GROUP BY)

## 📋 Before you start

- Make sure you have the `/files/week08/data/imdb_2025.db` file (already provided on Nuvolos).
- Use VS Code’s SQLite Viewer if you want to inspect the tables visually first.
- Run each cell in order — the SQL code builds on the previous sections.

## ⚙️ Imports

In [ ]:
import sqlite3
import pandas as pd

## 🔌 Connect to the database

We keep the connection object in a variable (`conn`). Every `pd.read_sql()` call needs it.

In [ ]:
DB_PATH = "./data/imdb_2025.db"
conn = sqlite3.connect(DB_PATH)
conn

### (Optional) Nuvolos managed connection

Uncomment the cell below *only if* Jon confirms Nuvolos Tables is enabled for this lecture.

In [ ]:
# from nuvolos import get_connection
# import pandas as pd
# conn = get_connection()
# conn

## 📚 Which tables exist?

Use SQLite’s catalog (`sqlite_master`) to confirm which tables exist.

In [ ]:
query = """
SELECT *
FROM sqlite_master
WHERE type = 'table'
ORDER BY name;
"""

tables = pd.read_sql(query, conn)
tables

## 1️⃣ SELECT basics

Pull a few rows from `title_basics` to remind ourselves what each column represents.

In [ ]:
query = """
SELECT
    *
FROM title_basics
LIMIT 5;
"""

pd.read_sql(query, conn)

The above is equivalent to a `pd.read_csv(<file-that-contains-title-basics.csv>).head(5)`.

`LIMIT` is the same as `head()`

**You can choose which fields to select:**

In [ ]:
query = """
SELECT
    tconst,
    primaryTitle,
    titleType,
    startYear,
    endYear
FROM title_basics
LIMIT 5;
"""

pd.read_sql(query, conn)

In pandas, this is equivalent to:

```python
(
    pd.read_csv(...)
    [['tconst', 'primaryTitle', 'titleType', 'startYear', 'endYear']]
    .head(5)
)

## 2️⃣ WHERE filtering

Filter to movies (`titleType = 'tvMiniSeries'`) released in 2025 so we connect the slide content to the keyboard.

In [ ]:
query = """
SELECT
    tconst,
    primaryTitle,
    titleType,
    startYear
FROM title_basics
WHERE titleType = 'tvMiniSeries' AND startYear = 2025
LIMIT 5;
"""

pd.read_sql(query, conn)

In pandas the query above could look like this:

```python
df_title_basics = pd.read_csv(...)[['tconst', 'primaryTitle', 'titleType', 'startYear', 'endYear']]
mask = df_title_basics['titleType'] == 'tvMiniSeries' & df_title_basics['startYear'] == 2025
df_title_basics[mask].head(5)
```

OR you could use the `query()` method:

```python
(
    pd.read_csv(...)
    [['tconst', 'primaryTitle', 'titleType', 'startYear', 'endYear']]
    .query("titleType == 'tvMiniSeries' & startYear == 2025")
    .head(5)
)
```

**A Hybrid Approach**

If you want, you can read the table first from the database into a pandas dataframe and handle the rest later in pandas:

In [ ]:
df_title_basics = pd.read_sql("SELECT * FROM title_basics", conn)

(
    df_title_basics[['tconst', 'primaryTitle', 'titleType', 'startYear', 'endYear']]
        .query("titleType == 'tvMiniSeries' & startYear == 2025")
        .head(5)
)

## 3️⃣ ORDER BY + LIMIT (title_ratings)

The `title_ratings` table stores `averageRating` and `numVotes`.

Let’s grab the most-loved titles (high rating and lots of votes) to match the slide demo.

In [ ]:
query = """
SELECT tconst, averageRating, numVotes
FROM title_ratings
WHERE numVotes > 100000
ORDER BY averageRating DESC
LIMIT 10;
"""

df_top_ratings = pd.read_sql(query, conn)
df_top_ratings

### Add the title names with pandas

We already loaded `title_basics`. Use `.isin()` to find the matching rows.

In [ ]:
df_titles = pd.read_sql(
    "SELECT tconst, primaryTitle, titleType FROM title_basics",
    conn
)

mask = df_titles["tconst"].isin(df_top_ratings["tconst"])
df_titles.loc[mask, ["tconst", "primaryTitle", "titleType"]]

`.isin()` compares each `tconst` in `df_titles` against the short list in `df_top_ratings`.
It returns `True` for matches, so `.loc[mask, ...]` shows only those rows.

### Combine both tables with `pd.merge`

This keeps the rating columns and the readable titles in one DataFrame.

In [ ]:
df_top = (
    pd.merge(
        df_top_ratings,
        df_titles,
        how="inner",
        on="tconst"
    )
    .sort_values("averageRating", ascending=False)
    .reset_index(drop=True)
)
df_top

### SQL JOIN equivalent

Same logic, written directly in SQL (and still executed via `pd.read_sql()`).

In [ ]:
pd.read_sql(
    """
    SELECT
        b.primaryTitle,
        r.averageRating,
        r.numVotes
    FROM title_ratings AS r
    JOIN title_basics AS b
      ON r.tconst = b.tconst
    WHERE r.numVotes > 100000
    ORDER BY r.averageRating DESC
    LIMIT 10;
    """,
    conn
)

## 🧠 Reflection prompt

- What changes if you sort by `numVotes` first?
- How would you join `title_ratings` with `title_basics` to show the title names?

## ✅ Close the connection when done

In [ ]:
conn.close()